# Imports & Constants

In [12]:

import os
import re
import warnings

import dask
import dask.bag as db
import featuretools as ft
import numpy as np
import pandas as pd
from IPython.display import display
from boruta import BorutaPy
from dask.distributed import Client, get_task_stream
from feature_engine.creation import CyclicalFeatures
from feature_engine.encoding import OneHotEncoder, RareLabelEncoder
from feature_engine.imputation import AddMissingIndicator, ArbitraryNumberImputer
from feature_engine.selection import (
    DropConstantFeatures, DropDuplicateFeatures, DropHighPSIFeatures,
    SmartCorrelatedSelection,
)
from featuretools.primitives import TimeSinceFirst, TimeSinceLast
from lightgbm import LGBMClassifier
from sklearn.ensemble import RandomForestClassifier
from sklearn.feature_selection import RFE
from tsfresh import extract_features
from woodwork.logical_types import Boolean, BooleanNullable, Categorical, Unknown

from utils_scoped import (
    add_calendar_values, preprocess_app_activity_data, read_app_activity, read_clients, read_communications,
    read_df_dtype, read_transactions, split_dataset_v2, write_df_dtype,
)

In [13]:
RANDOM_SEED = 42
NUM_WORKERS = 6
CHUNKS_NUM = 54

# DATA_BASE_DIR = 'data/'
RAW_DATA_DIR = 'data/raw/'
RAW_CHUNKS_DIR = 'data/raw_chunks/'
FEATURES_BASE_DIR = 'features/'
os.makedirs(FEATURES_BASE_DIR, exist_ok=True)

MIN_DATE_STR = '2024-12-01 00:00:00'
MAX_DATE_STR = '2025-09-01 00:00:00'

FEATURES_VERSION = 1

In [14]:
pd.set_option('display.float_format', '{:.3f}'.format)
pd.set_option('display.max_columns', None)

In [15]:
warnings.simplefilter(action='ignore', category=FutureWarning)
warnings.simplefilter(action='ignore', category=pd.errors.PerformanceWarning)

# Feature Engineering

## Package "featuretools"

### Create EntitySet

In [5]:
"""Clients"""

def add_clients_dataframes(es, path):
    clients_df = read_clients(path, encode_bool=False)
    clients_df = clients_df.astype({'client_id': str})
    display(clients_df.info())

    es.add_dataframe(
        clients_df,
        dataframe_name='clients',
        index='client_id',
        time_index='communication_month',
        logical_types={
            'client_id': Unknown,
            'target': Boolean,
            'is_train': Boolean,
        }
    )
    display(es['clients'].ww.schema)
    display(es)

In [6]:
"""Transactions"""

def add_transactions_dataframe(es, path):
    transactions_df = read_transactions(path, encode_bool=False, encode_category=False)
    transactions_df = transactions_df.astype({'client_id': str})
    transactions_df = add_calendar_values(transactions_df, 'tran_date', prefix='tran_date_')
    display(transactions_df.info())

    es.add_dataframe(
        transactions_df,
        dataframe_name='transactions',
        index='transaction_id',
        time_index='tran_date',
        make_index=True,
        logical_types={
            'client_id': Unknown,
            'cat_c2': Categorical,
            'cat_c3': Categorical,
            'cat_c4': Categorical,
            'fl_c6': Boolean,
            'fl_c7': Boolean,
            'fl_c8': Boolean,
            'fl_c9': Boolean,
            'fl_c10': Boolean,
            'fl_c11': Boolean,
            'fl_c12': Boolean,
            'fl_c13': Boolean,
            'fl_c14': Boolean,
            'fl_c15': Boolean,
        }
    )
    display(es['transactions'].ww.schema)

    es.add_relationship('clients', 'client_id', 'transactions', 'client_id')
    display(es)

In [7]:
"""App activity"""

def add_activities_dataframe(es, path):
    activities_df = read_app_activity(path, encode_bool=False, encode_category=False)
    activities_df = activities_df.astype({'client_id': str})
    activities_df = preprocess_app_activity_data(activities_df)
    activities_df = add_calendar_values(activities_df, 'activity_date', prefix='activity_date_')
    display(activities_df.info())

    es.add_dataframe(
        activities_df,
        dataframe_name='activities',
        index='activity_id',
        time_index='activity_date',
        make_index=True,
        logical_types={
            'client_id': Unknown,
            'cat_c3': Categorical,
            'cat_c4': Categorical,
            'cat_c5': Categorical,
            'cat_c6': Categorical,
            'cat_c9': Categorical,
            'cat_c8': BooleanNullable,
            'cat_c10': BooleanNullable,
        }
    )
    display(es['activities'].ww.schema)

    es.add_relationship('clients', 'client_id', 'activities', 'client_id')
    display(es)

In [8]:
"""Communications"""

def add_communications_dataframe(es, path):
    comms_df = read_communications(path, encode_category=False)
    comms_df = comms_df.astype({'client_id': str})
    comms_df = add_calendar_values(comms_df, 'contact_date', prefix='contact_date_')
    display(comms_df.info(show_counts=True))

    es.add_dataframe(
        comms_df,
        dataframe_name='comms',
        index='comm_id',
        time_index='contact_date',
        make_index=True,
        logical_types={
            'client_id': Unknown,
            'cat_c2': Categorical,
            'cat_c3': Categorical,
            'cat_c4': Categorical,
            'cat_c5': Categorical,
        }
    )
    display(es['comms'].ww.schema)

    es.add_relationship('clients', 'client_id', 'comms', 'client_id')
    display(es)

In [9]:
def entityset_from_partition(chunk_num: int, chunks_dir):
    es = ft.EntitySet(id='client_data')
    chunk_dir = os.path.join(chunks_dir, str(chunk_num))

    clients_path = os.path.join(chunk_dir, f'CLIENTS.csv')
    transactions_path = os.path.join(chunk_dir, f'TRANSACTIONS.csv')
    activities_path = os.path.join(chunk_dir, f'APP_ACTIVITY.csv')
    comms_path = os.path.join(chunk_dir, f'COMMUNICATIONS.csv')

    add_clients_dataframes(es, clients_path)
    add_transactions_dataframe(es, transactions_path)
    add_activities_dataframe(es, activities_path)
    add_communications_dataframe(es, comms_path)

    es.add_last_time_indexes()

    return {
        'es': es,
        'chunk_num': chunk_num,
    }

### Deep Feature Synthesis

In [10]:
"""Transactions"""

def prepare_dfs_transactions(es, primitive_options):
    df_name = 'transactions'

    # Date
    for prim in ['first', 'last']:
        primitive_options[prim]['include_columns'][df_name] += ['tran_date']
    primitive_options['mean']['include_columns'][df_name] += [
        'tran_date_day_of_week_sin', 'tran_date_day_of_week_cos',
        'tran_date_day_of_month_sin', 'tran_date_day_of_month_cos',
    ]

    # Numeric
    num_cols = ['float_c16', 'float_c17', 'float_c18', 'int_c19', 'float_c20', 'float_c21']
    for prim in ['mean', 'std', 'skew', 'kurtosis', 'min', 'max', 'sum']:
        primitive_options[prim]['include_columns'][df_name] += num_cols

    # Categorical
    cat_cols = list(es[df_name].ww.select(Categorical).columns)
    for prim in ['num_unique', 'mode', 'entropy']:
        primitive_options[prim]['include_columns'][df_name] += cat_cols

    # Boolean
    bool_cols = list(es[df_name].ww.select([Boolean, BooleanNullable]).columns)
    primitive_options['percent_true']['include_columns'][df_name] += bool_cols


    # Interesting values
    interesting_values = {
        'cat_c2': ['4', '14', '15'],
        'cat_c3': ['209', '303', '305', '314'],
        'int_c19': [-1, 1],
        'fl_c12': [True, False],
        'fl_c13': [True, False],
        'fl_c14': [True, False],
        'tran_date_is_weekend': [True, False],
    }
    es.add_interesting_values(dataframe_name=df_name, values=interesting_values)

In [11]:
"""Activities"""

def prepare_dfs_activities(es, primitive_options):
    df_name = 'activities'

    # Date
    for prim in ['first', 'last']:
        primitive_options[prim]['include_columns'][df_name] += ['activity_date']
    primitive_options['mean']['include_columns'][df_name] += [
        'activity_date_day_of_week_sin', 'activity_date_day_of_week_cos',
        'activity_date_day_of_month_sin', 'activity_date_day_of_month_cos',
    ]

    # Numeric
    num_cols = ['float_c11', 'float_c12', 'float_c13', 'float_c14', 'float_c15', 'float_c16', 'float_c17']
    for prim in ['mean', 'std', 'skew', 'kurtosis', 'min', 'max', 'sum']:
        primitive_options[prim]['include_columns'][df_name] += num_cols

    # Categorical
    cat_cols = list(es[df_name].ww.select(Categorical).columns)
    for prim in ['num_unique', 'mode', 'entropy']:
        primitive_options[prim]['include_columns'][df_name] += cat_cols

    # Boolean
    bool_cols = list(es[df_name].ww.select([Boolean, BooleanNullable]).columns)
    primitive_options['percent_true']['include_columns'][df_name] += bool_cols


    # Interesting values
    interesting_values = {
        'cat_c4': ['1', '2'],
        'cat_c6': ['1', '2', '3'],
        'cat_c9': ['1', '2'],
        'cat_c8': [True, False],
        'cat_c10': [True, False],
        'activity_date_is_weekend': [True, False],
    }
    es.add_interesting_values(dataframe_name=df_name, values=interesting_values)

In [12]:
"""Communications"""

def prepare_dfs_communications(es, primitive_options):
    df_name = 'comms'

    # Date
    for prim in ['first', 'last']:
        primitive_options[prim]['include_columns'][df_name] += ['contact_date']
    primitive_options['mean']['include_columns'][df_name] += [
        'contact_date_day_of_week_sin', 'contact_date_day_of_week_cos',
        'contact_date_day_of_month_sin', 'contact_date_day_of_month_cos',
    ]

    # Categorical
    cat_cols = list(es[df_name].ww.select(Categorical).columns)
    for prim in ['num_unique', 'mode', 'entropy']:
        primitive_options[prim]['include_columns'][df_name] += cat_cols

    # Boolean
    bool_cols = list(es[df_name].ww.select([Boolean, BooleanNullable]).columns)
    primitive_options['percent_true']['include_columns'][df_name] += bool_cols


    # Interesting values
    interesting_values = {
        'cat_c2': ['S3564', 'S3565', 'S3677', 'S3769'],
        'cat_c3': ['3', '4', '7'],
        'cat_c4': ['1', '2'],
        'cat_c5': ['4', '7'],
        'contact_date_is_weekend': [True, False],
    }
    es.add_interesting_values(dataframe_name=df_name, values=interesting_values)

In [13]:
AGG_PRIMITIVES = [
    'count',
    'first', 'last', TimeSinceFirst(unit='days'), TimeSinceLast(unit='days'),  # for date
    'mean', 'std', 'skew', 'kurtosis', 'min', 'max', 'sum',   # for numeric
    'num_unique', 'mode', 'entropy',  # for categorical
    'percent_true',  # for boolean
]

def prepare_dfs(es):
    primitive_options = {}
    for agg in AGG_PRIMITIVES:
         if agg not in ('count',) and isinstance(agg, str):
            primitive_options[agg]= {'include_columns': {}}
            for df_name in ('transactions', 'activities', 'comms'):
                 primitive_options[agg]['include_columns'][df_name] = []

    prepare_dfs_transactions(es, primitive_options)
    prepare_dfs_activities(es, primitive_options)
    prepare_dfs_communications(es, primitive_options)

    return primitive_options

In [14]:
"""Cut-off time dataframe"""

def get_cutoff_time(es):
    cutoff_df = es.dataframe_dict['clients'][['client_id', 'communication_month']].copy()
    cutoff_df.rename(columns={'communication_month': 'time'}, inplace=True)
    return cutoff_df

In [15]:
def run_dfs(es, primitive_options, cutoff_df):
    feature_matrix, feature_defs = ft.dfs(
        entityset=es,
        target_dataframe_name='clients',
        cutoff_time=cutoff_df,
        agg_primitives=AGG_PRIMITIVES,
        trans_primitives=['day', 'month', 'weekday', 'is_weekend'],
        where_primitives=['mean', 'sum', 'count', 'std', 'max', 'min', TimeSinceLast(unit='days')],
        primitive_options=primitive_options,
        max_depth=1,
        verbose=True,
        features_only=False,
        n_jobs=1,
        chunk_size=es.dataframe_dict['clients'].shape[0],
        return_types='all',
    )

    return feature_matrix, feature_defs

## Fixed windows

In [16]:
def compute_fixed_windows_features(es, fm, cutoff_df, primitive_options):
    df_windows = {
        'transactions': ['7 days', '14 days', '30 days', '90 days'],
        'activities': ['30 days', '90 days'],
        'comms': ['7 days', '14 days', '30 days'],
    }
    # df_windows = {
    #     'transactions': ['30 days', '90 days'],
    #     'activities': ['30 days', '90 days'],
    #     'comms': ['30 days'],
    # }
    for df_name, windows in df_windows.items():
        # Remove other dataframes from primitive options
        prim_opt_for_df = {prim: {'include_columns': {df_name: val.get('include_columns', {}).get(df_name, [])}} for prim, val in primitive_options.items()}

        for window in windows:
            fm_windows, _ = ft.dfs(
                entityset=es,
                target_dataframe_name='clients',
                ignore_columns={'clients': ['target', 'is_train', 'communication_month']},
                ignore_dataframes=list(set(es.dataframe_dict.keys()) - {df_name, 'clients'}),
                cutoff_time=cutoff_df,
                training_window=window,
                agg_primitives=['count', 'sum', 'mean', 'percent_true'],
                trans_primitives=[],
                where_primitives=['count', 'sum', 'mean'],
                primitive_options=prim_opt_for_df,
                max_depth=1,
                verbose=True,
                features_only=False,
                n_jobs=1,
                chunk_size=es.dataframe_dict['clients'].shape[0],
                return_types='all',
            )

            suffix = '__' + '_'.join(window.split())
            fm_windows = fm_windows.add_suffix(suffix)

            fm = fm.merge(fm_windows, on='client_id', how='left')

    return fm

## Exponential Moving Averages

In [17]:
def compute_ema_features_for_df(df, client_col, date_col, value_cols, spans=(30, 60, 90), prefix=''):
    out = []

    for client, sub in df.groupby(client_col):
        sub = sub.sort_values(date_col)
        row = {'client_id': client}

        for col in value_cols:
            for span in spans:
                row[f'{prefix}{col}__ema_{span}'] = (
                    sub[col].ewm(span=span, adjust=False).mean().iloc[-1]
                    if not sub[col].dropna().empty else np.nan
                )

        out.append(row)

    return pd.DataFrame(out)


def compute_ema_features(es, fm):
    transactions_df = es.dataframe_dict['transactions']
    activities_df = es.dataframe_dict['activities']

    transactions_num_cols = [c for c in transactions_df.columns if 'int' in c or 'float' in c]
    activities_num_cols = [c for c in activities_df.columns if 'int' in c or 'float' in c]

    tx_ema = compute_ema_features_for_df(transactions_df, 'client_id', 'tran_date', transactions_num_cols, prefix='transactions_')
    act_ema = compute_ema_features_for_df(activities_df, 'client_id', 'activity_date', activities_num_cols, prefix='activities_')

    fm = fm.merge(tx_ema, on='client_id', how='left')
    fm = fm.merge(act_ema, on='client_id', how='left')

    return fm

## Other features

In [18]:
def add_extra_unique_features(es, fm):
    transactions_df = es.dataframe_dict['transactions']
    activities_df = es.dataframe_dict['activities']
    comms_df = es.dataframe_dict['comms']

    transactions_df['tran_date_str'] = transactions_df['tran_date'].dt.date.astype('category')
    tx_dates_unique = transactions_df.groupby('client_id').agg(tran_date_str_nunique=('tran_date_str', 'nunique')).reset_index(names='client_id')

    activities_df['activity_date_str'] = activities_df['activity_date'].dt.date.astype('category')
    act_dates_unique = activities_df.groupby('client_id').agg(activity_date_str_nunique=('activity_date_str', 'nunique')).reset_index(names='client_id')
    act_devices_unique = activities_df.groupby('client_id').agg(device_id_nunique=('device_id', 'nunique')).reset_index(names='client_id')

    comms_df['contact_date_str'] = comms_df['contact_date'].dt.date.astype('category')
    comms_dates_unique = comms_df.groupby('client_id').agg(contact_date_str_nunique=('contact_date_str', 'nunique')).reset_index(names='client_id')

    fm = fm.merge(comms_dates_unique, on='client_id', how='left')
    fm = fm.merge(act_dates_unique, on='client_id', how='left')
    fm = fm.merge(act_devices_unique, on='client_id', how='left')
    fm = fm.merge(tx_dates_unique, on='client_id', how='left')

    return fm

In [19]:
def add_cross_table_interaction_features(es, fm):
    fm['INTERACTION_activity_per_trans'] = fm['COUNT(activities)'] / fm['COUNT(transactions)'].replace(0, 1)
    fm['INTERACTION_activity_per_trans__30_days'] = fm['COUNT(activities)__30_days'] / fm['COUNT(transactions)__30_days'].replace(0, 1)
    fm['INTERACTION_activity_per_trans__90_days'] = fm['COUNT(activities)__90_days'] / fm['COUNT(transactions)__90_days'].replace(0, 1)

    fm['INTERACTION_contact_per_trans'] = fm['COUNT(comms)'] / fm['COUNT(transactions)'].replace(0, 1)
    fm['INTERACTION_contact_per_trans__7_days'] = fm['COUNT(comms)__7_days'] / fm['COUNT(transactions)__7_days'].replace(0, 1)
    fm['INTERACTION_contact_per_trans__14_days'] = fm['COUNT(comms)__14_days'] / fm['COUNT(transactions)__14_days'].replace(0, 1)
    fm['INTERACTION_contact_per_trans__30_days'] = fm['COUNT(comms)__30_days'] / fm['COUNT(transactions)__30_days'].replace(0, 1)

    fm['INTERACTION_contact_per_activity'] = fm['COUNT(comms)'] / fm['COUNT(activities)'].replace(0, 1)
    fm['INTERACTION_contact_per_activity__30_days'] = fm['COUNT(comms)__30_days'] / fm['COUNT(activities)__30_days'].replace(0, 1)

    return fm

In [20]:
def add_financial_balance_features(es, fm):

    for tr_amount_col in ('float_c16', 'float_c18'):
        for period_days in (None, 7, 14, 30, 90):
            period_suffix = f'__{period_days}_days' if period_days else ''

            inflow = fm[f'SUM(transactions.{tr_amount_col} WHERE int_c19 = 1){period_suffix}']
            outflow = fm[f'SUM(transactions.{tr_amount_col} WHERE int_c19 = -1){period_suffix}']

            fm[f'BALANCE_{tr_amount_col}_net_flow{period_suffix}'] = inflow - outflow
            fm[f'BALANCE_{tr_amount_col}_savings_potential{period_suffix}'] = inflow / outflow.replace(0, 1)

            fm[f'BALANCE_{tr_amount_col}_disposable{period_suffix}'] = inflow - outflow
            fm[f'PRESSURE_{tr_amount_col}_outflow_to_inflow{period_suffix}'] = outflow / inflow.replace(0, 1)

            fm[f'FLAG_{tr_amount_col}_liquidity_positive{period_suffix}'] = fm[f'BALANCE_{tr_amount_col}_disposable{period_suffix}'] > 0

    return fm

In [21]:
def add_momentum_features(es, fm):

    for tr_amount_col in ('float_c16', 'float_c18'):
        for days_short, days_long in (('7', '30'), ('7', '90'), ('14', '30'), ('14', '90'), ('30', '90')):
            short = fm[f'MEAN(transactions.{tr_amount_col})__{days_short}_days']
            short_in = fm[f'MEAN(transactions.{tr_amount_col} WHERE int_c19 = 1)__{days_short}_days']
            short_out = fm[f'MEAN(transactions.{tr_amount_col} WHERE int_c19 = -1)__{days_short}_days']

            long = fm[f'MEAN(transactions.{tr_amount_col})__{days_long}_days']
            long_in = fm[f'MEAN(transactions.{tr_amount_col} WHERE int_c19 = 1)__{days_long}_days']
            long_out = fm[f'MEAN(transactions.{tr_amount_col} WHERE int_c19 = -1)__{days_long}_days']

            fm[f'MOMENTUM_tx_amount_{tr_amount_col}_7d_90d_ratio'] = short / long.replace(0, 1)
            fm[f'MOMENTUM_tx_amount_in_{tr_amount_col}_7d_90d_ratio'] = short_in / long_in.replace(0, 1)
            fm[f'MOMENTUM_tx_amount_out_{tr_amount_col}_7d_90d_ratio'] = short_out / long_out.replace(0, 1)

            fm[f'MOMENTUM_tx_amount_{tr_amount_col}_7d_minus_90d'] = short - long
            fm[f'MOMENTUM_tx_amount_in_{tr_amount_col}_7d_minus_90d'] = short_in - long_in
            fm[f'MOMENTUM_tx_amount_out_{tr_amount_col}_7d_minus_90d'] = short_out - long_out

            fm[f'FLAG_tx_{tr_amount_col}_accelerating'] = short > long
            fm[f'FLAG_tx_in_{tr_amount_col}_accelerating'] = short_in > long_in
            fm[f'FLAG_tx_out_{tr_amount_col}_accelerating'] = short_out > long_out

    return fm

## Add more time-series features

In [22]:
def prep_time_gaps(df, date_col, prefix):
    df = df.sort_values(by=['client_id', date_col])

    gap_col_name = f'{prefix}_gap_days'
    df[gap_col_name] = df.groupby('client_id')[date_col].diff().dt.total_seconds() / (3600 * 24)
    df[gap_col_name] = df[gap_col_name].fillna(0)

    return df[['client_id', date_col, gap_col_name]]


def add_time_series_features(es, fm):
    transactions_df = es.dataframe_dict['transactions']
    activities_df = es.dataframe_dict['activities']
    comms_df = es.dataframe_dict['comms']

    df_transactions_ts = prep_time_gaps(transactions_df, 'tran_date', 'tran_date')
    df_transactions_ts['float_c16_diff'] = transactions_df.groupby('client_id')['float_c16'].diff().fillna(0)  # difference between transactions amount
    df_transactions_ts['float_c18_diff'] = transactions_df.groupby('client_id')['float_c18'].diff().fillna(0)  # difference between transactions amount
    df_activities_ts = prep_time_gaps(activities_df, 'activity_date', 'activity_date')
    df_comms_ts  = prep_time_gaps(comms_df, 'contact_date', 'contact_date')

    display(df_transactions_ts.head(10))

    datasets = {
        'transactions': (df_transactions_ts, 'tran_date', ['tran_date_gap_days', 'float_c16_diff', 'float_c18_diff']),
        'activities': (df_activities_ts, 'activity_date', ['activity_date_gap_days']),
        'communications': (df_comms_ts, 'contact_date', ['contact_date_gap_days'])
    }
    all_features = []
    for name, (df, date_col, val_cols) in datasets.items():
        print(f'Processing {name}...')

        for val_col in val_cols:
            fc_parameters = {
                'median': None,
                'mean': None,
                'maximum': None,
                'minimum': None,
                'standard_deviation': None,
                'skewness': None,
                'kurtosis': None,
                'quantile': [
                    {'q': 0.1},
                    {'q': 0.25},
                    {'q': 0.75},
                    {'q': 0.9}
                ],
                'linear_trend': [{'attr': 'slope'}],
                'approximate_entropy': [{'m': 2, 'r': 0.25}],
                'ratio_beyond_r_sigma': [{'r': 2}],
                'autocorrelation': [{'lag': 1}],
                'fft_aggregated': [{'aggtype': 'centroid'}, {'aggtype': 'variance'}],
                'longest_strike_above_mean': None,
                'longest_strike_below_mean': None,
                'count_above_mean': None,
            }
            features = extract_features(
                timeseries_container=df,
                column_id='client_id',
                column_sort=date_col,
                column_value=val_col,
                default_fc_parameters=fc_parameters,
                n_jobs=1,
                # chunksize=es.dataframe_dict['clients'].shape[0],
            )
            features = features.reset_index(names='client_id')
            all_features.append(features)

    for features in all_features:
        fm = fm.merge(features, on='client_id', how='left')

    return fm

## Main method

In [23]:
FM_CHUNKS_OUTPUT_DIR = os.path.join(FEATURES_BASE_DIR, f'fm_chunks_v{FEATURES_VERSION}/')

os.makedirs(FM_CHUNKS_OUTPUT_DIR, exist_ok=True)

In [24]:
def feature_matrix_from_entityset(es_dict, save=True):
    es = es_dict['es']
    chunk_num = es_dict['chunk_num']

    primitive_options = prepare_dfs(es)
    cutoff_df = get_cutoff_time(es)

    fm, fd = run_dfs(es, primitive_options, cutoff_df)
    display(fd)
    display(fm.head())
    display(fm.info(verbose=True, show_counts=True))
    display(fm.describe())

    # fm = compute_ratios_for_periods(es, fm, cutoff_df, primitive_options)
    fm = compute_fixed_windows_features(es, fm, cutoff_df, primitive_options)
    fm = compute_ema_features(es, fm)
    fm = add_extra_unique_features(es, fm)
    fm = add_cross_table_interaction_features(es, fm)
    fm = add_financial_balance_features(es, fm)
    fm = add_momentum_features(es, fm)
    fm = add_time_series_features(es, fm)

    display(fm.info(verbose=True, show_counts=True))

    if save:
        # chunk_dir = os.path.join(FM_OUTPUT_DIR, str(es_dict['chunk_num']))
        # os.makedirs(chunk_dir, exist_ok=True)
        fm_output_path = os.path.join(FM_CHUNKS_OUTPUT_DIR, f'feature_matrix_{chunk_num}.csv')
        fm.to_csv(fm_output_path, index=False)

        dtype_output_path = os.path.join(FM_CHUNKS_OUTPUT_DIR, f'fm_dtype_{chunk_num}.json')
        write_df_dtype(fm, dtype_output_path)

In [ ]:
"""For testing purposes only"""

# es_dict = entityset_from_partition(1, RAW_CHUNKS_DIR)
# fm = feature_matrix_from_entityset(es_dict, save=True)

## Compute with Dask

In [25]:
dask.config.set({
    'distributed.worker.memory.target': 0.70,
    'distributed.worker.memory.spill': 0.85,
    'distributed.worker.memory.pause': 0.90,
    'distributed.worker.memory.terminate': False,
})
client = Client(
    n_workers=NUM_WORKERS,
    threads_per_worker=1,
    memory_limit='16GB'
)
print(f'Dask Dashboard available at: {client.dashboard_link}')

Dask Dashboard available at: http://127.0.0.1:8787/status


In [26]:
chunks_nums = list(range(1, CHUNKS_NUM + 1))
b = dask.bag.from_sequence(chunks_nums, npartitions=CHUNKS_NUM)  # specify npartitions explicitly to avoid auto-grouping
b = b.map(entityset_from_partition, chunks_dir=RAW_CHUNKS_DIR)
b = b.map(feature_matrix_from_entityset)
display(b)

dask.bag<feature_matrix_from_entityset, npartitions=54>

In [27]:
with get_task_stream() as ts:
    result = b.compute()

history = pd.DataFrame(ts.data)
display(history)

stimulus_id                 worker  nbytes  \
0    task-finished-1769419010.1755142  tcp://127.0.0.1:52762     104   
1    task-finished-1769419014.9545622  tcp://127.0.0.1:52754     104   
2     task-finished-1769419027.422221  tcp://127.0.0.1:52755     104   
3    task-finished-1769419032.1091783  tcp://127.0.0.1:52752     104   
4      task-finished-1769419043.23144  tcp://127.0.0.1:52744     104   
..                                ...                    ...     ...   
104  task-finished-1769421059.5460024  tcp://127.0.0.1:52754     104   
105   task-finished-1769421059.548259  tcp://127.0.0.1:52754     104   
106  task-finished-1769421065.8972015  tcp://127.0.0.1:52755     104   
107  task-finished-1769421065.8987653  tcp://127.0.0.1:52755     104   
108   task-finished-1769421065.912443  tcp://127.0.0.1:52754    1432   

                                                  type typename metadata  \
0    b'\x80\x05\x95\x15\x00\x00\x00\x00\x00\x00\x00...     list       {}   
1    b'\x80\x05\x95\x15\x00\x00\x00\x00\x00\x00\x00...     list       {}   
2    b'\x80\x05\x95\x15\x00\x00\x00\x00\x00\x00\x00...     list       {}   
3    b'\x80\x05\x95\x15\x00\x00\x00\x00\x00\x00\x00...     list       {}   
4    b'\x80\x05\x95\x15\x00\x00\x00\x00\x00\x00\x00...     list       {}   
..                                                 ...      ...      ...   
104  b'\x80\x05\x95\x15\x00\x00\x00\x00\x00\x00\x00...     list       {}   
105  b'\x80\x05\x95\x15\x00\x00\x00\x00\x00\x00\x00...     list       {}   
106  b'\x80\x05\x95\x15\x00\x00\x00\x00\x00\x00\x00...     list       {}   
107  b'\x80\x05\x95\x15\x00\x00\x00\x00\x00\x00\x00...     list       {}   
108  b'\x80\x05\x95\x15\x00\x00\x00\x00\x00\x00\x00...     list       {}   

     thread                                         startstops status  \
0     46496  ({'action': 'compute', 'start': 1769418677.894...     OK   
1     61148  ({'action': 'compute', 'start': 1769418677.925...     OK   
2     30624  ({'action': 'compute', 'start': 1769418678.086...     OK   
3     20688  ({'action': 'compute', 'start': 1769418677.937...     OK   
4     33528  ({'action': 'compute', 'start': 1769418677.925...     OK   
..      ...                                                ...    ...   
104   61148  ({'action': 'compute', 'start': 1769420870.482...     OK   
105   61148  ({'action': 'compute', 'start': 1769421059.542...     OK   
106   30624  ({'action': 'compute', 'start': 1769420886.467...     OK   
107   30624  ({'action': 'compute', 'start': 1769421065.891...     OK   
108   61148  ({'action': 'transfer', 'start': 1769421065.90...     OK   

                                                   key  
0    (entityset_from_partition-from_sequence-featur...  
1    (entityset_from_partition-from_sequence-featur...  
2    (entityset_from_partition-from_sequence-featur...  
3    (entityset_from_partition-from_sequence-featur...  
4    (entityset_from_partition-from_sequence-featur...  
..                                                 ...  
104  (entityset_from_partition-from_sequence-featur...  
105  (feature_matrix_from_entityset-8c15c628e6e1344...  
106  (entityset_from_partition-from_sequence-featur...  
107  (feature_matrix_from_entityset-8c15c628e6e1344...  
108  finalize-hlgfinalizecompute-e5277fa47960447491...  

[109 rows x 10 columns]

In [28]:
client.close()

## Compose Feature Matrix (from chunks)

In [29]:
RAW_FM_OUT_PATH = os.path.join(FEATURES_BASE_DIR, f'features_v{FEATURES_VERSION}_raw.csv')
RAW_FM_DTYPE_OUT_PATH = os.path.join(FEATURES_BASE_DIR, f'features_v{FEATURES_VERSION}_raw_dtype.json')

In [31]:
fms = []
for i in chunks_nums:
    path = os.path.join(FM_CHUNKS_OUTPUT_DIR, f'feature_matrix_{i}.csv')
    dtype_path = os.path.join(FM_CHUNKS_OUTPUT_DIR, f'fm_dtype_{i}.json')
    fm_dtype, date_cols = read_df_dtype(dtype_path)
    fms.append(pd.read_csv(path, dtype=fm_dtype, parse_dates=date_cols))

feature_matrix = pd.concat(fms, axis=0)
feature_matrix.to_csv(RAW_FM_OUT_PATH, index=False)
write_df_dtype(feature_matrix, RAW_FM_DTYPE_OUT_PATH)

## Postprocessing

In [32]:
FEATURES_OUT_PATH = os.path.join(FEATURES_BASE_DIR, f'features_v{FEATURES_VERSION}.csv')

In [33]:
def handle_missing_values(df):
    df = df.dropna(subset=[
        # Transactions
        'tran_date_str_nunique', 'STD(transactions.float_c18)',
        # Activities
        'activity_date_str_nunique', 'STD(activities.float_c11)',
        # Comms
        'contact_date_str_nunique',
    ])

    null_mask = df.isnull()
    cols_with_nulls = null_mask.columns[null_mask.any()].tolist()

    mean_like = [c for c in cols_with_nulls if c.startswith('MEAN(')]
    std_like = [c for c in cols_with_nulls if c.startswith('STD(')]
    min_like = [c for c in cols_with_nulls if c.startswith('MIN(')]
    max_like = [c for c in cols_with_nulls if c.startswith('MAX(')]
    pct_true_like = [c for c in cols_with_nulls if c.startswith('PERCENT_TRUE(')]
    tslike = [c for c in cols_with_nulls if c.startswith('TIME_SINCE_LAST(')]
    skew_like = [c for c in cols_with_nulls if (
        c.startswith('SKEW(') or
        c.endswith('__skewness') or
        '__autocorrelation' in c or
        '__fft_aggregated__aggtype' in c or
        c.endswith('__kurtosis')
    )]
    momentum_ratio = [c for c in cols_with_nulls if c.startswith('MOMENTUM_') and 'ratio' in c]
    momentum_minus = [c for c in cols_with_nulls if c.startswith('MOMENTUM_') and 'minus' in c]

    missing_ind_candidates = mean_like + std_like + min_like + max_like + skew_like
    missing_rates = null_mask.mean()
    add_missing_ind_cols = [c for c in missing_ind_candidates if missing_rates[c] > 0.05]
    if add_missing_ind_cols:
        ami = AddMissingIndicator(variables=add_missing_ind_cols)
        df = ami.fit_transform(df)

    impute_0 = pct_true_like + mean_like + std_like + min_like + max_like + skew_like + momentum_minus
    if impute_0:
        ami = ArbitraryNumberImputer(arbitrary_number=0, variables=impute_0)
        df = ami.fit_transform(df)

    impute_1 = momentum_ratio
    if impute_1:
        ami = ArbitraryNumberImputer(arbitrary_number=1, variables=impute_1)
        df = ami.fit_transform(df)

    impute_9999 = tslike
    if impute_9999:
        ami = ArbitraryNumberImputer(arbitrary_number=9999, variables=impute_9999)
        df = ami.fit_transform(df)

    return df

def convert_dates(df):
    """Convert dates to days from initial point"""
    for date_col in df.select_dtypes(include=['datetime64[ns]']).columns:
        df[date_col + '_days'] = (df[date_col] - pd.to_datetime(MIN_DATE_STR)).dt.days
        df = df.drop(columns=[date_col])
    return df

def encode_cyclical_features(df):
    """Encode cyclical features (e.g. day of week, month)"""
    time_cols = ['DAY(communication_month)', 'MONTH(communication_month)', 'WEEKDAY(communication_month)']
    df = df.astype({col: 'int8' for col in time_cols})
    cyclical = CyclicalFeatures(variables=time_cols, drop_original=True)
    df = cyclical.fit_transform(df)
    return df

def encode_categorical_features(df):
    top_n_categ = {
        # Transactions
        'MODE(transactions.cat_c2)': 4,
        'MODE(transactions.cat_c3)': 6,
        'MODE(transactions.cat_c4)': 1,

        # Activities
        'MODE(activities.cat_c3)': 1,
        'MODE(activities.cat_c4)': 1,
        'MODE(activities.cat_c5)': 1,
        'MODE(activities.cat_c6)': 5,
        'MODE(activities.cat_c9)': 2,

        # Communications
        'MODE(comms.cat_c2)': 10,
        'MODE(comms.cat_c3)': 1,
        'MODE(comms.cat_c4)': 2,
        'MODE(comms.cat_c5)': 1,
    }
    for col, top_n in top_n_categ.items():
        rle = RareLabelEncoder(tol=0, n_categories=1, max_n_categories=top_n, variables=[col])
        df = rle.fit_transform(df)

    ohe = OneHotEncoder(variables=list(top_n_categ.keys()))
    df = ohe.fit_transform(df)

    return df

def convert_boolean_values(df):
    """Convert boolean values to 0 and 1"""
    df = df.astype({col: 'int8' for col in df.select_dtypes(include=['bool']).columns})
    df = df.astype({col: 'Int8' for col in df.select_dtypes(include=['boolean']).columns})
    return df

In [16]:
# df_dtype, df_date_cols = read_df_dtype(RAW_FM_DTYPE_OUT_PATH)
# df = pd.read_csv(RAW_FM_OUT_PATH, dtype=df_dtype, parse_dates=df_date_cols)
df = feature_matrix

df = handle_missing_values(df)
df = convert_dates(df)
df = encode_cyclical_features(df)
df = encode_categorical_features(df)
df = convert_boolean_values(df)

# Replace special characters (LightGBM is sensitive to them)
df = df.rename(columns=lambda x: re.sub(r'[,\n\[\]\{\}:"]', '__', x))

df.to_csv(FEATURES_OUT_PATH, index=False)
display(df.info(verbose=True, show_counts=True))
display(df.describe())

<class 'pandas.core.frame.DataFrame'>
Index: 34964 entries, 0 to 36336
Data columns (total 4197 columns):
 #     Column                                                                                             Non-Null Count  Dtype  
---    ------                                                                                             --------------  -----  
 0     client_id                                                                                          34964 non-null  object 
 1     target                                                                                             34964 non-null  int8   
 2     is_train                                                                                           34964 non-null  int8   
 3     COUNT(transactions)                                                                                34964 non-null  Int64  
 4     ENTROPY(transactions.cat_c2)                                                                       34964 no

None

target  is_train  COUNT(transactions)  ENTROPY(transactions.cat_c2)  \
count 34964.000 34964.000            34964.000                     34964.000   
mean      0.245     0.793              447.722                         1.574   
std       0.430     0.405              474.128                         0.403   
min       0.000     0.000                2.000                         0.000   
25%       0.000     1.000              122.000                         1.329   
50%       0.000     1.000              309.000                         1.621   
75%       0.000     1.000              616.000                         1.855   
max       1.000     1.000             8721.000                         2.721   

       ENTROPY(transactions.cat_c3)  ENTROPY(transactions.cat_c4)  \
count                     34964.000                     34964.000   
mean                          1.643                         0.106   
std                           0.453                         0.191   
min                           0.000                         0.000   
25%                           1.359                         0.000   
50%                           1.674                         0.016   
75%                           1.944                         0.127   
max                           3.290                         2.159   

       KURTOSIS(transactions.float_c16)  KURTOSIS(transactions.float_c17)  \
count                         34964.000                         34964.000   
mean                             78.719                           132.415   
std                             146.909                           225.167   
min                              -2.000                            -2.000   
25%                               0.000                             0.000   
50%                              27.624                            34.186   
75%                              93.020                           176.602   
max                            3572.596                          2741.303   

       KURTOSIS(transactions.float_c18)  KURTOSIS(transactions.float_c20)  \
count                         34964.000                         34964.000   
mean                             42.100                            16.053   
std                              57.951                           112.541   
min                              -2.000                            -2.000   
25%                              11.096                             0.000   
50%                              25.523                             0.000   
75%                              51.168                             0.000   
max                            1350.809                          3767.000   

       KURTOSIS(transactions.float_c21)  KURTOSIS(transactions.int_c19)  \
count                         34964.000                       34964.000   
mean                             43.426                          -0.719   
std                              62.417                           2.654   
min                              -2.000                          -2.000   
25%                              11.074                          -1.807   
50%                              25.791                          -1.328   
75%                              52.145                          -0.380   
max                            1588.049                         259.670   

       MAX(transactions.float_c16)  MAX(transactions.float_c17)  \
count                    34964.000                    34964.000   
mean                         1.620                        4.577   
std                          4.868                       19.215   
min                          0.000                        0.000   
25%                          0.000                        0.000   
50%                          0.470                        1.000   
75%                          1.660                        4.010   
max                        413.130                     2294.720   

# Features Selection

In [35]:
FEATURES_PATH = os.path.join(FEATURES_BASE_DIR, f'features_v{FEATURES_VERSION}.csv')

features_df = pd.read_csv(FEATURES_PATH)

In [36]:
clients_cols = ['client_id', 'target', 'is_train']
clients_data = features_df[clients_cols]

X = features_df.drop(columns=clients_cols)
y = features_df['target']

In [37]:
X_train, _, _, y_train, _, _ = split_dataset_v2(FEATURES_PATH, valid_size=0.2)

## Filters

In [38]:
"""Constant features"""

drop_constant = DropConstantFeatures(tol=1)
drop_constant.fit(X_train)
X1 = drop_constant.transform(X)
X1_train = drop_constant.transform(X_train)

In [39]:
"""Quasi-constant features"""

drop_quasi = DropConstantFeatures(tol=0.99)
drop_quasi.fit(X1_train)
X2 = drop_quasi.transform(X1)
X2_train = drop_quasi.transform(X1_train)

In [40]:
"""Duplicate features"""

drop_duplicates = DropDuplicateFeatures()
drop_duplicates.fit(X2_train)
X3 = drop_duplicates.transform(X2)
X3_train = drop_duplicates.transform(X2_train)

In [44]:
"""PCI"""

psi_selector = DropHighPSIFeatures(
    split_frac=0.8,
    # cut_off=datetime(2025, 4, 1),
    strategy='equal_frequency',
    bins=10,
    threshold=0.1,
)

psi_selector.fit(X3_train)
X_psi = psi_selector.transform(X3)
X_psi_train = psi_selector.transform(X3_train)

In [45]:
"""Correlation"""

corr_selector = SmartCorrelatedSelection(
    method='pearson',
    threshold=0.7,
    selection_method='missing_values',
    # selection_method='model_performance',
    # scoring='roc_auc',
    # estimator=lgb_est,
)

corr_selector.fit(X_psi_train, y_train)
X_corr = corr_selector.transform(X_psi)
X_corr_train = corr_selector.transform(X_psi_train)

In [46]:
X_filtered = X_corr
X_filtered_train = X_corr_train
display(X_filtered.info(verbose=True, show_counts=True))
display(X_filtered.describe())

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 34964 entries, 0 to 34963
Data columns (total 841 columns):
 #    Column                                                                                           Non-Null Count  Dtype  
---   ------                                                                                           --------------  -----  
 0    COUNT(transactions)                                                                              34964 non-null  int64  
 1    ENTROPY(transactions.cat_c2)                                                                     34964 non-null  float64
 2    ENTROPY(transactions.cat_c4)                                                                     34964 non-null  float64
 3    KURTOSIS(transactions.float_c16)                                                                 34964 non-null  float64
 4    KURTOSIS(transactions.float_c17)                                                                 34964 non-null  float64
 

None

COUNT(transactions)  ENTROPY(transactions.cat_c2)  \
count            34964.000                     34964.000   
mean               447.722                         1.574   
std                474.128                         0.403   
min                  2.000                         0.000   
25%                122.000                         1.329   
50%                309.000                         1.621   
75%                616.000                         1.855   
max               8721.000                         2.721   

       ENTROPY(transactions.cat_c4)  KURTOSIS(transactions.float_c16)  \
count                     34964.000                         34964.000   
mean                          0.106                            78.719   
std                           0.191                           146.909   
min                           0.000                            -2.000   
25%                           0.000                             0.000   
50%                           0.016                            27.624   
75%                           0.127                            93.020   
max                           2.159                          3572.596   

       KURTOSIS(transactions.float_c17)  KURTOSIS(transactions.float_c18)  \
count                         34964.000                         34964.000   
mean                            132.415                            42.100   
std                             225.167                            57.951   
min                              -2.000                            -2.000   
25%                               0.000                            11.096   
50%                              34.186                            25.523   
75%                             176.602                            51.168   
max                            2741.303                          1350.809   

       KURTOSIS(transactions.float_c20)  KURTOSIS(transactions.int_c19)  \
count                         34964.000                       34964.000   
mean                             16.053                          -0.719   
std                             112.541                           2.654   
min                              -2.000                          -2.000   
25%                               0.000                          -1.807   
50%                               0.000                          -1.328   
75%                               0.000                          -0.380   
max                            3767.000                         259.670   

       MAX(transactions.float_c16)  MAX(transactions.float_c17)  \
count                    34964.000                    34964.000   
mean                         1.620                        4.577   
std                          4.868                       19.215   
min                          0.000                        0.000   
25%                          0.000                        0.000   
50%                          0.470                        1.000   
75%                          1.660                        4.010   
max                        413.130                     2294.720   

       MAX(transactions.float_c18)  MAX(transactions.float_c20)  \
count                    34964.000                    34964.000   
mean                      1442.860                       80.753   
std                       1647.169                      487.185   
min                          0.010                        0.000   
25%                        502.500                        0.000   
50%                       1000.000                        0.000   
75%                       1950.000                        0.000   
max                      55600.000                    13500.000   

       MEAN(transactions.float_c16)  MEAN(transactions.float_c17)  \
count                     34964.000                     34964.000   
mean                          0.030                         0.091   
std                    

In [47]:
FEAT_SEL_FILTERED_OUT_PATH = os.path.join(FEATURES_BASE_DIR, f'features_v{FEATURES_VERSION}_filtered_v1.csv')

pd.concat([X_filtered, clients_data], axis=1).to_csv(FEAT_SEL_FILTERED_OUT_PATH, index=False)

## Boruta selection

In [102]:
rf_est = RandomForestClassifier(
    class_weight='balanced',
    max_depth=5,
    n_jobs=NUM_WORKERS,
    random_state=RANDOM_SEED,
)

feat_selector = BorutaPy(
    rf_est,
    n_estimators='auto',
    perc=100,
    max_iter=150,
    verbose=2,
    random_state=RANDOM_SEED,
)

feat_selector.fit(X_filtered_train.values, y_train.values)

accepted_features = X_filtered_train.columns[feat_selector.support_].to_list()
tentative_features = X_filtered_train.columns[feat_selector.support_weak_].to_list()

X_boruta = X_filtered[accepted_features + tentative_features]
X_boruta_train = X_filtered_train[accepted_features + tentative_features]

Iteration: 	1 / 150
Confirmed: 	0
Tentative: 	841
Rejected: 	0
Iteration: 	2 / 150
Confirmed: 	0
Tentative: 	841
Rejected: 	0
Iteration: 	3 / 150
Confirmed: 	0
Tentative: 	841
Rejected: 	0
Iteration: 	4 / 150
Confirmed: 	0
Tentative: 	841
Rejected: 	0
Iteration: 	5 / 150
Confirmed: 	0
Tentative: 	841
Rejected: 	0
Iteration: 	6 / 150
Confirmed: 	0
Tentative: 	841
Rejected: 	0
Iteration: 	7 / 150
Confirmed: 	0
Tentative: 	841
Rejected: 	0
Iteration: 	8 / 150
Confirmed: 	218
Tentative: 	205
Rejected: 	418
Iteration: 	9 / 150
Confirmed: 	218
Tentative: 	205
Rejected: 	418
Iteration: 	10 / 150
Confirmed: 	218
Tentative: 	205
Rejected: 	418
Iteration: 	11 / 150
Confirmed: 	218
Tentative: 	205
Rejected: 	418
Iteration: 	12 / 150
Confirmed: 	224
Tentative: 	145
Rejected: 	472
Iteration: 	13 / 150
Confirmed: 	224
Tentative: 	145
Rejected: 	472
Iteration: 	14 / 150
Confirmed: 	224
Tentative: 	145
Rejected: 	472
Iteration: 	15 / 150
Confirmed: 	224
Tentative: 	145
Rejected: 	472
Iteration: 	16 / 

In [103]:
FEAT_SEL_BORUTA_OUT_PATH = os.path.join(FEATURES_BASE_DIR, f'features_v{FEATURES_VERSION}_boruta_md5_perc100_iter150.csv')

pd.concat([X_boruta, clients_data], axis=1).to_csv(FEAT_SEL_BORUTA_OUT_PATH, index=False)

In [118]:
"""Boruta import"""

# BORUTA_IN_PATH = os.path.join(FEATURES_BASE_DIR, f'features_v{FEATURES_VERSION}_boruta_md5_perc100_iter150.csv')
#
# boruta_features_df = pd.read_csv(BORUTA_IN_PATH).drop(columns=clients_cols)
# boruta_features_df = boruta_features_df.rename(columns=lambda x: re.sub(r'[,\n\[\]\{\}:"]', '__', x))
# boruta_cols = boruta_features_df.columns.tolist()
#
# X_boruta = X[boruta_cols]
# X_boruta_train = X_train[boruta_cols]

## RFE

In [144]:
# V1
rfe_est = LGBMClassifier(
    boosting_type='gbdt',
    objective='binary',
    importance_type='gain',
    n_estimators=1334,
    learning_rate=0.02976,
    max_depth=3,
    num_leaves=3,
    min_child_samples=215,
    subsample=0.68114,
    colsample_bytree=0.78928,
    bagging_fraction=0.61835,
    bagging_freq=1,
    reg_alpha=5.0,
    reg_lambda=5.0,
    class_weight=None,
    verbosity=-1,
    n_jobs=NUM_WORKERS,
    random_state=RANDOM_SEED,
)


# V4
# rfe_est = LGBMClassifier(
#     boosting_type='gbdt',
#     objective='binary',
#     importance_type='gain',
#     max_depth=3,
#     num_leaves=5,
#     min_child_samples=100,
#     reg_alpha=0.5,
#     reg_lambda=0.5,
#     n_estimators=500,
#     learning_rate=0.05,
#     subsample=0.7,
#     colsample_bytree=0.8,
#     n_jobs=NUM_WORKERS,
#     random_state=RANDOM_SEED
# )

In [145]:
rfe = RFE(
    estimator=rfe_est,
    n_features_to_select=50,
    step=2,
    verbose=1,
)
rfe.fit(X_boruta_train, y_train)

selected_rfe_features = X_boruta.columns[rfe.get_support()]
X_rfe = X_boruta[selected_rfe_features]
X_rfe_train = X_boruta_train[selected_rfe_features]

Fitting estimator with 247 features.
Fitting estimator with 245 features.
Fitting estimator with 243 features.
Fitting estimator with 241 features.
Fitting estimator with 239 features.
Fitting estimator with 237 features.
Fitting estimator with 235 features.
Fitting estimator with 233 features.
Fitting estimator with 231 features.
Fitting estimator with 229 features.
Fitting estimator with 227 features.
Fitting estimator with 225 features.
Fitting estimator with 223 features.
Fitting estimator with 221 features.
Fitting estimator with 219 features.
Fitting estimator with 217 features.
Fitting estimator with 215 features.
Fitting estimator with 213 features.
Fitting estimator with 211 features.
Fitting estimator with 209 features.
Fitting estimator with 207 features.
Fitting estimator with 205 features.
Fitting estimator with 203 features.
Fitting estimator with 201 features.
Fitting estimator with 199 features.
Fitting estimator with 197 features.
Fitting estimator with 195 features.
F

In [146]:
FEAT_SEL_RFE_OUT_PATH = os.path.join(FEATURES_BASE_DIR, f'features_v{FEATURES_VERSION}_boruta_perc_100_rfe_step2_lgb_v1.csv')

pd.concat([X_rfe, clients_data], axis=1).to_csv(FEAT_SEL_RFE_OUT_PATH, index=False)